# Babylonian sqrt

I would like to use a simple example, computation of sqrt(x), where for me how autodiff works came as both a mathematical surprise, and a computing wonder. The example is the Babylonian algorithm, known to man for millenia, to compute sqrt(x):

> **Repeat** $t \leftarrow \frac{(t + \frac{x}{t})}{2}$ **until** $t$ **converges to** $\sqrt{x}$.

Each iteration has one add and two divides. For illustration purposes, 10 iterations suffice.


In [3]:
function Babylonian(x; N = 10)
    t = (1 + x) / 2
    for i = 2:N; t = (t + x/t) / 2 end
    t
end

Babylonian (generic function with 1 method)

In [4]:
using ForwardDiff

In [5]:
ForwardDiff.derivative(Babylonian, 2), .5/sqrt(2)

(0.35355339059327373, 0.35355339059327373)

In [6]:
α = π  # Type \alpha+<tab> to get the symbol
Babylonian(α), √α

(1.7724538509055159, 1.7724538509055159)

In [8]:
x=2
Babylonian(x), √x

(1.414213562373095, 1.4142135623730951)

In [9]:
using Plots
plotly()

Plots.PlotlyBackend()

In [11]:
i = 0:.01:49

plot([x->Babylonian(x, N=i) for i=1:5], i, label=["Iteration $j" for i=1:1, j=1:5])
plot!(sqrt, i, c="black", label="sqrt",
      title = "Those Babylonians really knew how to √")

### ... and now the derivative, almost by magic

In [17]:
struct D <:Number # D is a function-derivative pair
    f::Tuple{Float64, Float64}
end

In [18]:
D(1,2)

D((1.0, 2.0))

In [19]:
D(x,y) = D((x,y)) # overload D to take in either a tupe

D

In [22]:
D(1,2) + D(3,4)

LoadError: + not defined for D

### ... but we need to define atomic operations

Sum Rule: $(x + y)' = x' + y'$

Quotient Rule: $(\frac{x}{y})' = \frac{(y x' - x y')}{y^2}$

In [25]:
import Base: +, /, convert, promote_rule

+(x::D, y::D) = D(x.f .+ y.f)
/(x::D, y::D) = D((x.f[1]/y.f[1], (y.f[1]*x.f[2] - x.f[1]*y.f[2])/y.f[1]^2))

convert(::Type{D}, x::Real) = D((x, zero(x)))
promote_rule(::Type{D}, ::Type{<:Number}) = D

promote_rule (generic function with 163 methods)

In [28]:
D(2,3) + D(3,4), D(2,3) / D(3,4)

(D((5.0, 7.0)), D((0.6666666666666666, 0.1111111111111111)))

In [31]:
x=49; Babylonian(D(x,1)), (√x, .5/√x) # magic

(D((7.0, 0.07142857142857142)), (7.0, 0.07142857142857142))

In [32]:
x=π; Babylonian(D(x,1)), (√x, .5/√x) # magic

(D((1.7724538509055159, 0.28209479177387814)), (1.7724538509055159, 0.28209479177387814))

In [33]:
i = .2:.01:49
plot([x->Babylonian(D((x, 1.0)),N=i).f[2] for i=1:5], i)
plot!(x->.5/√x, i, c="black", label="d(sqrt(x))/dx",
      title = "Babylonians Differentiated")

# It just works!

How does it work? We will explain in a moment. Right now marvel that it does. Note we did not import any autodiff package. **Everything** is just basic vanilla Julia.

# Symbolically

We haven't yet explained how it works, but it may be of some value to understand that the below is mathematically equivalent, though not what the computation is doing.

Notice in the below that Babylonian works on SymPy symbols.

In [36]:
using SymPy

In [37]:
x = symbols("x")

display("Iterations as a function of x")
for k = 1:5
    display(simplify(Babylonian(x, N=k)))
end

display("Derivatives as a function of x")
for k = 1:5
    display(simplify(diff(simplify(Babylonian(x, N=k)), x)))
end

"Iterations as a function of x"

x   1
- + -
2   2

           2
    (x + 1) 
x + --------
       4    
------------
   x + 1    

 4       3       2           
x  + 28*x  + 70*x  + 28*x + 1
-----------------------------
     / 3      2          \   
   8*\x  + 7*x  + 7*x + 1/   

 8        7         6         5          4         3         2            
x  + 120*x  + 1820*x  + 8008*x  + 12870*x  + 8008*x  + 1820*x  + 120*x + 1
--------------------------------------------------------------------------
         / 7       6        5        4        3        2           \      
      16*\x  + 35*x  + 273*x  + 715*x  + 715*x  + 273*x  + 35*x + 1/      

...

1/2

   2            
  x  + 2*x + 5  
----------------
  / 2          \
4*\x  + 2*x + 1/

 6       5        4        3        2             
x  + 14*x  + 147*x  + 340*x  + 375*x  + 126*x + 21
--------------------------------------------------
  / 6       5       4        3       2           \
8*\x  + 14*x  + 63*x  + 100*x  + 63*x  + 14*x + 1/

 14       13         12          11           10            9            8    
x   + 70*x   + 3199*x   + 52364*x   + 438945*x   + 2014506*x  + 5430215*x  + 8
------------------------------------------------------------------------------
      / 14       13         12          11           10           9           
   16*\x   + 70*x   + 1771*x   + 20540*x   + 126009*x   + 440986*x  + 920795*x

        7            6            5            4           3          2       
836200*x  + 8842635*x  + 5425210*x  + 2017509*x  + 437580*x  + 52819*x  + 3094
------------------------------------------------------------------------------
8            7           6           5           4          3         2       
  + 1173960*x  + 920795*x  + 440986*x  + 126009*x  + 20540*x  + 1771*x  + 70*x

       
*x + 85
-------
    \  
 + 1/  

 30        29          28            27              26               25      
x   + 310*x   + 59799*x   + 4851004*x   + 215176549*x   + 5809257090*x   + 102
------------------------------------------------------------------------------
                     / 30        29          28            27             26  
                  32*\x   + 310*x   + 36611*x   + 2161196*x   + 73961629*x   +

           24                  23                   22                   21   
632077611*x   + 1246240871640*x   + 10776333438765*x   + 68124037776390*x   + 
------------------------------------------------------------------------------
             25                24                 23                  22      
 1603620018*x   + 23367042639*x   + 238538538360*x   + 1758637118685*x   + 957

                 20                     19                     18             
321156247784955*x   + 1146261110726340*x   + 3133113888931089*x   + 6614351291
--------------------------------------------------

# How autodiff is getting the answer...

Let us by hand take the "derivative" of the Babylonian iteration with respect to x. Specifically t′ = dt/dx

In [39]:
function dBabylonian(x; N = 10)
    t = (1 + x) / 2
    t′ = 1 / 2
    for i = 1:N
        t = (t + x/t) / 2
        t′ = (t′ + (t - x * t′) / t^2) / 2
    end
    t′
end

dBabylonian (generic function with 1 method)

In [40]:
x=π; dBabylonian(x), .5/√x # magic

(0.2820947917738782, 0.28209479177387814)

What just happened? Answer: We created an iteration by hand for t′ given our iteration for t. Then we ran the iteration alongside the iteration for t.

In [41]:
Babylonian(D((x,1)))

D((1.7724538509055159, 0.28209479177387814))

How did this work? It created the same derivative iteration, using very general rules that are set once and need not be written by hand.

**Important:** The derivative is substituted before the JIT compiler, and thus efficient compiled code is executed.

# Dual Number Notation

Instead of D(a,b) we can write a + bε, where ε satisfies ε^2=0. (Some people like to recall imaginary numbers where an i is introduced with i^2=-1.)

Others like to think of how engineers just drop the O(ε^2) terms.

The four rules are

$$(a + b\epsilon) \pm (c + d\epsilon) = (a \pm c) + (b \pm d)\epsilon$$

$$(a + b\epsilon) * (c + d\epsilon) = (ac) + (bc + ad)\epsilon$$

$$(a + b\epsilon) / (c + d\epsilon) = (a/c) + \frac{(bc - ad)}{c^2}\epsilon$$

In [42]:
@syms a b c d ϵ

(a, b, c, d, ϵ)

In [45]:
series((a + b*ϵ) + (c + d*ϵ), ϵ, 0, 2)

a + c + ϵ*(b + d)

In [43]:
series((a + b*ϵ) / (c + d*ϵ), ϵ, 0, 2)

  /  a*d   b\   a    / 2\
ϵ*|- --- + -| + - + O\ϵ /
  |    2   c|   c        
  \   c     /            

In [44]:
series((a + b*ϵ) * (c + d*ϵ), ϵ, 0, 2)

                       / 2\
ϵ*(a*d + b*c) + a*c + O\ϵ /

In [46]:
Base.show(io::IO, x::D) = print(io, x.f[1], " + ", x.f[2], " ϵ")

In [48]:
D(1,2)

1.0 + 2.0 ϵ

In [49]:
# Add the last two rules
import Base: -, *

-(x::D, y::D) = D(x.f .- y.f)
*(x::D, y::D) = D((x.f[1]*y.f[1], (x.f[2]*y.f[1] + x.f[1]*y.f[2])))

* (generic function with 348 methods)

In [51]:
D(2,1)^2

4.0 + 4.0 ϵ

In [52]:
ϵ = D(0,1)

0.0 + 1.0 ϵ

In [55]:
ϵ * ϵ, ϵ^2

(0.0 + 0.0 ϵ, 0.0 + 0.0 ϵ)

In [56]:
1/(1+ϵ) # Exact power series: 1-ϵ+ϵ²-ϵ³-...

1.0 + -1.0 ϵ

In [57]:
(1+ϵ)^5 # Note this just works (we didn't train powers)!

1.0 + 5.0 ϵ

In [58]:
(1+ϵ)^(-1)

1.0 + -1.0 ϵ

** Ref: https://www.youtube.com/watch?v=5F6roh4pmJU